# 🚀 KEEN 新架構交互式測試 / Interactive New Architecture Test

本筆記本提供了一個交互式環境來測試 KEEN 的新架構。您可以：
- 使用 Widget 選擇要分析的檔案
- 測試 INT 和 DAT 檔案的載入和分析
- 使用 Plotly 進行數據視覺化

This notebook provides an interactive environment to test KEEN's new architecture. You can:
- Use widgets to select files for analysis
- Test loading and analysis of INT and DAT files
- Visualize data using Plotly

## 📚 1. 初始化和導入 / Initialization and Imports

In [1]:
import sys
import os
from pathlib import Path
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import ipywidgets as widgets
from IPython.display import display, HTML, clear_output
import logging

# 添加後端路徑 / Add backend path
backend_path = Path().absolute()
if backend_path.name != 'backend':
    backend_path = backend_path.parent
sys.path.insert(0, str(backend_path))

# 導入新架構模組 / Import new architecture modules
from core.experiment_session import ExperimentSession
from core.data_models import TopoData, CitsData, StsData, TxtData
from core.visualization.spm_plots import SPMPlotting
from core.visualization.spectroscopy_plots import SpectroscopyPlotting

# 設置日誌 / Setup logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

print("✅ 模組導入成功 / Modules imported successfully")
print(f"📁 工作目錄: {Path().absolute()}")
print(f"📁 Working directory: {Path().absolute()}")

✅ 模組導入成功 / Modules imported successfully
📁 工作目錄: /Users/yangziliang/Git-Projects/keen/backend/test
📁 Working directory: /Users/yangziliang/Git-Projects/keen/backend/test


## 📂 2. 選擇實驗檔案 / Select Experiment File

In [2]:
# 搜尋 testfile 目錄中的 TXT 檔案 / Search for TXT files in testfile directory
testfile_dir = backend_path.parent / "testfile"
txt_files = list(testfile_dir.glob("*.txt"))

if not txt_files:
    print("❌ 未找到 TXT 檔案 / No TXT files found")
    print(f"請確保 {testfile_dir} 目錄中有 .txt 檔案")
else:
    print(f"✅ 找到 {len(txt_files)} 個 TXT 檔案 / Found {len(txt_files)} TXT files")
    
    # 創建檔案選擇器 / Create file selector
    file_options = [(f.name, str(f)) for f in txt_files]
    file_selector = widgets.Dropdown(
        options=file_options,
        description='選擇檔案:',
        style={'description_width': 'initial'},
        layout=widgets.Layout(width='500px')
    )
    
    display(file_selector)
    
    # 全局變數用於存儲會話 / Global variable to store session
    current_session = None

✅ 找到 1 個 TXT 檔案 / Found 1 TXT files


Dropdown(description='選擇檔案:', layout=Layout(width='500px'), options=(('20250521_Janus Stacking SiO2_13K_113.tx…

## 🔧 3. 載入實驗會話 / Load Experiment Session

In [ ]:
def load_experiment_session(txt_file_path):
    """載入實驗會話 / Load experiment session"""
    try:
        session = ExperimentSession(txt_file_path)
        
        # 顯示會話摘要 / Display session summary
        summary = session.get_session_summary()
        
        print(f"🎯 實驗名稱: {session.experiment_name}")
        print(f"🎯 Experiment name: {session.experiment_name}")
        print(f"📊 檔案摘要 / File summary:")
        
        files_summary = summary['files_summary']['available']
        for file_type, count in files_summary.items():
            if count > 0:
                print(f"   - {file_type.upper()}: {count}")
        
        return session
        
    except Exception as e:
        print(f"❌ 載入失敗 / Loading failed: {str(e)}")
        return None

# 載入按鈕 / Load button
load_button = widgets.Button(
    description='🚀 載入實驗 / Load Experiment',
    button_style='primary',
    layout=widgets.Layout(width='200px')
)

output_area = widgets.Output()

def on_load_clicked(b):
    global current_session
    with output_area:
        clear_output()
        if hasattr(file_selector, 'value') and file_selector.value:
            current_session = load_experiment_session(file_selector.value)
            if current_session:
                print("\n✅ 實驗會話載入成功! / Experiment session loaded successfully!")
        else:
            print("❌ 請先選擇一個檔案 / Please select a file first")

load_button.on_click(on_load_clicked)

display(load_button, output_area)

Button(button_style='primary', description='🚀 載入實驗 / Load Experiment', layout=Layout(width='200px'), style=But…

Output()

## 📁 4. 瀏覽可用檔案 / Browse Available Files

In [4]:
def display_available_files():
    """顯示可用檔案 / Display available files"""
    if current_session is None:
        print("❌ 請先載入實驗會話 / Please load experiment session first")
        return
    
    available_files = current_session.available_files
    
    print("📋 可用檔案列表 / Available Files List:")
    print("=" * 60)
    
    for file_type, file_list in available_files.items():
        if file_list:
            print(f"\n📂 {file_type.upper()} 檔案 ({len(file_list)} 個):")
            for i, file_key in enumerate(file_list, 1):
                try:
                    file_proxy = current_session[file_key]
                    info = file_proxy.file_info
                    signal_type = info.signal_type if info else "Unknown"
                    direction = info.direction if info else ""
                    size = info.human_readable_size if info else "Unknown"
                    print(f"   {i:2d}. {file_key}")
                    print(f"       訊號: {signal_type} {direction} | 大小: {size}")
                except Exception as e:
                    print(f"   {i:2d}. {file_key} (載入錯誤: {str(e)})")

# 瀏覽檔案按鈕 / Browse files button
browse_button = widgets.Button(
    description='📁 瀏覽檔案 / Browse Files',
    button_style='info',
    layout=widgets.Layout(width='200px')
)

browse_output = widgets.Output()

def on_browse_clicked(b):
    with browse_output:
        clear_output()
        display_available_files()

browse_button.on_click(on_browse_clicked)

display(browse_button, browse_output)

Button(button_style='info', description='📁 瀏覽檔案 / Browse Files', layout=Layout(width='200px'), style=ButtonSty…

Output()

## 🗺️ 5. 拓撲圖分析和視覺化 / Topography Analysis and Visualization

In [5]:
# 重新載入模組以獲取最新修復 / Reload modules to get latest fixes
import importlib
import core.visualization.spm_plots
import core.visualization.spectroscopy_plots

# 重新載入視覺化模組
importlib.reload(core.visualization.spm_plots)
importlib.reload(core.visualization.spectroscopy_plots)

# 重新導入類別
from core.visualization.spm_plots import SPMPlotting
from core.visualization.spectroscopy_plots import SpectroscopyPlotting

print("✅ 視覺化模組已重新載入 / Visualization modules reloaded successfully")
print("📝 注意：如果仍有錯誤，請重新啟動 kernel 並重新執行所有 cells")

✅ 視覺化模組已重新載入 / Visualization modules reloaded successfully
📝 注意：如果仍有錯誤，請重新啟動 kernel 並重新執行所有 cells


In [6]:
# 測試原始 INT 數據的 Plotly 繪圖 / Test raw INT data plotting with Plotly
print("🔍 測試原始數據繪圖方向 / Testing raw data plotting orientation")
print("=" * 50)

# 1. 創建一個簡單的測試圖像 / Create a simple test image
test_image = np.zeros((10, 10))
test_image[0:3, :] = 1  # 頂部三行 / Top three rows
test_image[:, 0:3] = 2  # 左側三列 / Left three columns
test_image[0:3, 0:3] = 3  # 左上角 / Top-left corner

print("測試圖像結構 / Test image structure:")
print("- 左上角 (3) / Top-left corner (3)")
print("- 頂部橫條 (1) / Top horizontal bar (1)")
print("- 左側豎條 (2) / Left vertical bar (2)")
print("- 其餘部分 (0) / Rest (0)")

# 2. 使用不同方法繪製 / Plot using different methods
from plotly.subplots import make_subplots

fig = make_subplots(rows=1, cols=3, subplot_titles=[
    "方法1: 默認 Plotly / Default Plotly",
    "方法2: Y軸反轉 / Y-axis reversed", 
    "方法3: 數據翻轉 / Data flipped"
])

# 方法1: 默認 Plotly / Default Plotly
fig.add_trace(go.Heatmap(z=test_image, colorscale='Viridis', showscale=False), row=1, col=1)

# 方法2: Y軸反轉 / Y-axis reversed
fig.add_trace(go.Heatmap(z=test_image, colorscale='Viridis', showscale=False), row=1, col=2)

# 方法3: 數據翻轉 / Data flipped
fig.add_trace(go.Heatmap(z=np.flipud(test_image), colorscale='Viridis', showscale=False), row=1, col=3)

# 更新 Y 軸設置 / Update Y-axis settings
fig.update_yaxes(autorange='reversed', row=1, col=2)  # 反轉 Y 軸

fig.update_layout(height=400, width=1200, title_text="圖像方向測試 / Image Orientation Test")
fig.show()

print("\n結論 / Conclusion:")
print("- 方法1顯示 Plotly 默認將數據第一行放在底部")
print("- 方法2通過反轉 Y 軸解決問題")
print("- 方法3通過翻轉數據解決問題")

🔍 測試原始數據繪圖方向 / Testing raw data plotting orientation
測試圖像結構 / Test image structure:
- 左上角 (3) / Top-left corner (3)
- 頂部橫條 (1) / Top horizontal bar (1)
- 左側豎條 (2) / Left vertical bar (2)
- 其餘部分 (0) / Rest (0)



結論 / Conclusion:
- 方法1顯示 Plotly 默認將數據第一行放在底部
- 方法2通過反轉 Y 軸解決問題
- 方法3通過翻轉數據解決問題


In [7]:
# 直接測試 INT 檔案數據 / Direct test with INT file data
print("🔬 直接測試 INT 檔案數據繪圖 / Direct INT file data plotting test")
print("=" * 50)

if current_session and current_session.get_topo_files():
    # 獲取第一個拓撲檔案 / Get first topography file
    topo_key = current_session.get_topo_files()[0]
    topo = current_session[topo_key]
    data = topo.data
    
    print(f"測試檔案 / Test file: {topo_key}")
    print(f"圖像尺寸 / Image shape: {data.shape}")
    print(f"物理尺寸 / Physical size: {data.x_range:.2f} × {data.y_range:.2f} nm")
    
    # 創建比較圖 / Create comparison plots
    fig = make_subplots(rows=1, cols=2, subplot_titles=[
        "當前方法 / Current Method",
        "修正後 (Y軸反轉) / Fixed (Y-axis reversed)"
    ])
    
    # 當前方法 / Current method
    x = np.linspace(0, data.x_range, data.x_pixels)
    y = np.linspace(0, data.y_range, data.y_pixels)
    
    fig.add_trace(go.Heatmap(
        z=data.image,
        x=x, y=y,
        colorscale='RdYlBu_r',
        showscale=False
    ), row=1, col=1)
    
    # 修正方法 / Fixed method
    fig.add_trace(go.Heatmap(
        z=data.image,
        x=x, y=y,
        colorscale='RdYlBu_r',
        showscale=True
    ), row=1, col=2)
    
    # 只對第二個子圖反轉 Y 軸 / Reverse Y-axis only for second subplot
    fig.update_yaxes(autorange='reversed', row=1, col=2)
    
    # 設置軸標籤和比例 / Set axis labels and aspect ratio
    for col in [1, 2]:
        fig.update_xaxes(title_text="X (nm)", row=1, col=col)
        fig.update_yaxes(title_text="Y (nm)", scaleanchor=f"x{col}", scaleratio=1, row=1, col=col)
    
    fig.update_layout(
        height=500, 
        width=1000, 
        title_text=f"INT 檔案方向比較: {topo_key}"
    )
    fig.show()
    
    print("\n分析 / Analysis:")
    print("- 左圖：當前實現（可能上下顛倒）")
    print("- 右圖：Y軸反轉後的正確方向")
    print("\n如果右圖看起來正確，我們需要在 SPMPlotting 中添加 Y 軸反轉")
else:
    print("❌ 請先載入實驗會話 / Please load experiment session first")

INFO:core.parsers.int_parser:INT 檔案解析成功: /Users/yangziliang/Git-Projects/keen/testfile/20250521_Janus Stacking SiO2_13K_113TopoFwd.int
INFO:core.type_managers.TopoManager:檔案載入成功: 20250521_Janus Stacking SiO2_13K_113TopoFwd


🔬 直接測試 INT 檔案數據繪圖 / Direct INT file data plotting test
測試檔案 / Test file: 20250521_Janus Stacking SiO2_13K_113TopoFwd
圖像尺寸 / Image shape: (500, 500)
物理尺寸 / Physical size: 10.00 × 10.00 nm



分析 / Analysis:
- 左圖：當前實現（可能上下顛倒）
- 右圖：Y軸反轉後的正確方向

如果右圖看起來正確，我們需要在 SPMPlotting 中添加 Y 軸反轉


In [8]:
# 測試修復後的 SPMPlotting / Test fixed SPMPlotting
print("🔧 測試修復後的 SPM 繪圖函數 / Testing fixed SPM plotting function")
print("=" * 50)

# 重新載入模組以獲取修復 / Reload module to get fix
from core.visualization.spm_plots import SPMPlotting

if current_session and current_session.get_topo_files():
    topo_key = current_session.get_topo_files()[0]
    topo = current_session[topo_key]
    data = topo.data
    
    print(f"使用修復後的 SPMPlotting 測試: {topo_key}")
    
    # 使用修復後的 SPMPlotting / Use fixed SPMPlotting
    fig = SPMPlotting.plot_topography(
        image_data=data.image,
        physical_scale=(data.x_range, data.y_range),
        title=f"修復後的拓撲圖 / Fixed Topography - {topo_key}",
        width=600,
        height=600
    )
    
    fig.show()
    
    print("✅ 如果圖像現在方向正確，說明修復成功！")
    print("✅ If the image orientation is now correct, the fix is successful!")
else:
    print("❌ 請先載入實驗會話 / Please load experiment session first")

🔧 測試修復後的 SPM 繪圖函數 / Testing fixed SPM plotting function
使用修復後的 SPMPlotting 測試: 20250521_Janus Stacking SiO2_13K_113TopoFwd


✅ 如果圖像現在方向正確，說明修復成功！
✅ If the image orientation is now correct, the fix is successful!


In [9]:
def create_topo_selector():
    """創建拓撲檔案選擇器 / Create topography file selector"""
    if current_session is None:
        return widgets.HTML("❌ 請先載入實驗會話 / Please load experiment session first")
    
    topo_files = current_session.get_topo_files()
    if not topo_files:
        return widgets.HTML("❌ 沒有找到拓撲檔案 / No topography files found")
    
    # 創建選項，包含檔案資訊 / Create options with file info
    options = []
    for file_key in topo_files:
        try:
            file_proxy = current_session[file_key]
            info = file_proxy.file_info
            signal_type = info.signal_type if info else "Unknown"
            direction = info.direction if info else ""
            label = f"{file_key} ({signal_type} {direction})"
            options.append((label, file_key))
        except:
            options.append((file_key, file_key))
    
    return widgets.Dropdown(
        options=options,
        description='選擇拓撲檔案:',
        style={'description_width': 'initial'},
        layout=widgets.Layout(width='600px')
    )

def plot_topography(file_key, flatten=False):
    """繪製拓撲圖 / Plot topography"""
    try:
        topo = current_session[file_key]
        data = topo.data
        
        if not isinstance(data, TopoData):
            print(f"❌ {file_key} 不是拓撲檔案 / Not a topography file")
            return
        
        # 選擇要顯示的圖像 / Choose image to display
        if flatten and data.flattened is not None:
            image = data.flattened
            title = f"Flattened Topography - {file_key}"
        else:
            image = data.image
            title = f"Raw Topography - {file_key}"
        
        # 使用 SPMPlotting 繪製 / Plot using SPMPlotting
        fig = SPMPlotting.plot_topography(
            image_data=image,
            physical_scale=(data.x_range, data.y_range),
            title=title,
            width=700,
            height=600
        )
        
        # 顯示統計資訊 / Display statistics
        print(f"📊 檔案資訊 / File Information:")
        print(f"   尺寸: {data.shape}")
        print(f"   物理範圍: {data.x_range:.2f} × {data.y_range:.2f} nm")
        print(f"   像素尺度: {data.pixel_scale_x:.4f} × {data.pixel_scale_y:.4f} nm/pixel")
        print(f"   高度範圍: {image.min():.3f} ~ {image.max():.3f}")
        print(f"   高度 RMS: {np.std(image):.3f}")
        
        return fig
        
    except Exception as e:
        print(f"❌ 繪圖錯誤 / Plotting error: {str(e)}")
        import traceback
        traceback.print_exc()
        return None

# 創建拓撲分析介面 / Create topography analysis interface
print("🗺️ 拓撲圖分析工具 / Topography Analysis Tool")
print("=" * 50)

# 檔案選擇器 / File selector
topo_selector = create_topo_selector()

# 平坦化選項 / Flattening option
flatten_checkbox = widgets.Checkbox(
    value=False,
    description='使用平坦化圖像 / Use flattened image',
    style={'description_width': 'initial'}
)

# 繪圖按鈕 / Plot button
plot_topo_button = widgets.Button(
    description='🗺️ 繪製拓撲圖 / Plot Topography',
    button_style='success',
    layout=widgets.Layout(width='200px')
)

topo_output = widgets.Output()

def on_plot_topo_clicked(b):
    with topo_output:
        clear_output()
        if hasattr(topo_selector, 'value') and topo_selector.value:
            fig = plot_topography(topo_selector.value, flatten_checkbox.value)
            if fig:
                fig.show()
        else:
            print("❌ 請選擇拓撲檔案 / Please select a topography file")

plot_topo_button.on_click(on_plot_topo_clicked)

display(topo_selector)
display(flatten_checkbox)
display(plot_topo_button)
display(topo_output)

🗺️ 拓撲圖分析工具 / Topography Analysis Tool


Dropdown(description='選擇拓撲檔案:', layout=Layout(width='600px'), options=(('20250521_Janus Stacking SiO2_13K_113T…

Checkbox(value=False, description='使用平坦化圖像 / Use flattened image', style=CheckboxStyle(description_width='init…

Button(button_style='success', description='🗺️ 繪製拓撲圖 / Plot Topography', layout=Layout(width='200px'), style=B…

Output()

## 🔬 6. CITS 數據分析和視覺化 / CITS Data Analysis and Visualization

In [10]:
def create_cits_selector():
    """創建 CITS 檔案選擇器 / Create CITS file selector"""
    if current_session is None:
        return widgets.HTML("❌ 請先載入實驗會話 / Please load experiment session first")
    
    cits_files = current_session.get_cits_files()
    if not cits_files:
        return widgets.HTML("❌ 沒有找到 CITS 檔案 / No CITS files found")
    
    options = [(file_key, file_key) for file_key in cits_files]
    
    return widgets.Dropdown(
        options=options,
        description='選擇 CITS 檔案:',
        style={'description_width': 'initial'},
        layout=widgets.Layout(width='600px')
    )

def plot_cits_bias_slice(file_key, bias_index=0):
    """繪製 CITS 偏壓切片 / Plot CITS bias slice"""
    try:
        cits = current_session[file_key]
        data = cits.data
        
        if not isinstance(data, CitsData):
            print(f"❌ {file_key} 不是 CITS 檔案 / Not a CITS file")
            return
        
        # 獲取偏壓切片 / Get bias slice
        bias_slice = data.get_bias_slice(bias_index)
        bias_value = data.bias_values[bias_index]
        
        # 繪製 / Plot
        fig = go.Figure()
        
        fig.add_trace(go.Heatmap(
            z=bias_slice,
            colorscale='RdYlBu_r',
            showscale=True,
            hovertemplate='X: %{x}<br>Y: %{y}<br>Current: %{z:.3e}<extra></extra>'
        ))
        
        fig.update_layout(
            title=f"CITS Bias Slice - {file_key}<br>Bias: {bias_value:.1f} mV",
            xaxis_title="X (pixels)",
            yaxis_title="Y (pixels)",
            width=600,
            height=600,
            template="plotly_white",
            # 保持長寬比 / Maintain aspect ratio  
            yaxis=dict(scaleanchor="x", scaleratio=1)
        )
        
        # 顯示統計資訊 / Display statistics
        print(f"📊 CITS 檔案資訊 / CITS File Information:")
        print(f"   3D 數據尺寸: {data.shape}")
        print(f"   偏壓點數: {data.n_bias_points}")
        print(f"   偏壓範圍: {data.bias_range[0]:.1f} ~ {data.bias_range[1]:.1f} mV")
        print(f"   網格大小: {data.grid_size}")
        print(f"   當前偏壓: {bias_value:.1f} mV (索引 {bias_index})")
        print(f"   電流範圍: {bias_slice.min():.3e} ~ {bias_slice.max():.3e}")
        
        return fig
        
    except Exception as e:
        print(f"❌ CITS 繪圖錯誤 / CITS plotting error: {str(e)}")
        import traceback
        traceback.print_exc()
        return None

def plot_cits_iv_curve(file_key, x_pixel, y_pixel):
    """繪製 CITS I-V 曲線 / Plot CITS I-V curve"""
    try:
        cits = current_session[file_key]
        data = cits.data
        
        if not isinstance(data, CitsData):
            print(f"❌ {file_key} 不是 CITS 檔案 / Not a CITS file")
            return
        
        # 提取 I-V 曲線 / Extract I-V curve
        iv_data = data.data_3d[:, y_pixel, x_pixel]
        bias_values = data.bias_values
        
        # 繪製 I-V 曲線 / Plot I-V curve
        fig = go.Figure()
        
        fig.add_trace(go.Scatter(
            x=bias_values,
            y=iv_data,
            mode='lines+markers',
            name=f'I-V at ({x_pixel}, {y_pixel})',
            line=dict(width=2),
            marker=dict(size=4)
        ))
        
        fig.update_layout(
            title=f"I-V Curve - {file_key}<br>Position: ({x_pixel}, {y_pixel})",
            xaxis_title="Bias (mV)",
            yaxis_title="Current (A)",
            width=700,
            height=500,
            template="plotly_white"
        )
        
        # 顯示統計資訊 / Display statistics
        print(f"📊 I-V 曲線資訊 / I-V Curve Information:")
        print(f"   位置: ({x_pixel}, {y_pixel})")
        print(f"   電流範圍: {iv_data.min():.3e} ~ {iv_data.max():.3e} A")
        print(f"   電流 RMS: {np.std(iv_data):.3e} A")
        
        return fig
        
    except Exception as e:
        print(f"❌ I-V 曲線繪圖錯誤 / I-V curve plotting error: {str(e)}")
        import traceback
        traceback.print_exc()
        return None

# 創建 CITS 分析介面 / Create CITS analysis interface
print("🔬 CITS 數據分析工具 / CITS Data Analysis Tool")
print("=" * 50)

# 檔案選擇器 / File selector
cits_selector = create_cits_selector()

# 偏壓索引選擇器 / Bias index selector
bias_index_slider = widgets.IntSlider(
    value=0,
    min=0,
    max=len(current_session[cits_selector.value].data.bias_values) - 1 if cits_selector.value else 0,
    step=1,
    description='偏壓索引:',
    style={'description_width': 'initial'},
    layout=widgets.Layout(width='400px')
)

# 像素位置選擇器 / Pixel position selectors
x_pixel_slider = widgets.IntSlider(
    value=50,
    min=0,
    max=99,
    step=1,
    description='X 像素:',
    style={'description_width': 'initial'},
    layout=widgets.Layout(width='300px')
)

y_pixel_slider = widgets.IntSlider(
    value=50,
    min=0,
    max=99,
    step=1,
    description='Y 像素:',
    style={'description_width': 'initial'},
    layout=widgets.Layout(width='300px')
)

# 按鈕 / Buttons
plot_bias_button = widgets.Button(
    description='🗺️ 繪製偏壓切片 / Plot Bias Slice',
    button_style='success',
    layout=widgets.Layout(width='250px')
)

plot_iv_button = widgets.Button(
    description='📈 繪製 I-V 曲線 / Plot I-V Curve',
    button_style='warning',
    layout=widgets.Layout(width='250px')
)

cits_output = widgets.Output()

def on_plot_bias_clicked(b):
    with cits_output:
        clear_output()
        if hasattr(cits_selector, 'value') and cits_selector.value:
            fig = plot_cits_bias_slice(cits_selector.value, bias_index_slider.value)
            if fig:
                fig.show()
        else:
            print("❌ 請選擇 CITS 檔案 / Please select a CITS file")

def on_plot_iv_clicked(b):
    with cits_output:
        clear_output()
        if hasattr(cits_selector, 'value') and cits_selector.value:
            fig = plot_cits_iv_curve(cits_selector.value, x_pixel_slider.value, y_pixel_slider.value)
            if fig:
                fig.show()
        else:
            print("❌ 請選擇 CITS 檔案 / Please select a CITS file")

plot_bias_button.on_click(on_plot_bias_clicked)
plot_iv_button.on_click(on_plot_iv_clicked)

display(cits_selector)
display(bias_index_slider)
display(widgets.HBox([x_pixel_slider, y_pixel_slider]))
display(widgets.HBox([plot_bias_button, plot_iv_button]))
display(cits_output)

INFO:core.parsers.dat_parser:開始解析 DAT 檔案: /Users/yangziliang/Git-Projects/keen/testfile/20250521_Janus Stacking SiO2_13K_113It_to_PC_Matrix.dat


🔬 CITS 數據分析工具 / CITS Data Analysis Tool


/Users/yangziliang/Git-Projects/keen/backend/core/parsers/dat_parser.py:84: DtypeWarning:

Columns (0,1,2) have mixed types. Specify dtype option on import or set low_memory=False.

INFO:core.parsers.dat_parser:掃描方向判斷結果: downward
INFO:core.parsers.dat_parser:CITS 數據處理完成: 100×100 網格，401 個偏壓點，downward 掃描
INFO:core.parsers.dat_parser:DAT 檔案解析完成: CITS 模式
INFO:core.type_managers.CitsManager:檔案載入成功: 20250521_Janus Stacking SiO2_13K_113It_to_PC_Matrix


Dropdown(description='選擇 CITS 檔案:', layout=Layout(width='600px'), options=(('20250521_Janus Stacking SiO2_13K_…

IntSlider(value=0, description='偏壓索引:', layout=Layout(width='400px'), max=400, style=SliderStyle(description_w…

Output()

## 🔧 7. 分析功能測試 / Analysis Functions Test

In [11]:
def test_topography_analysis():
    """測試拓撲圖分析功能 / Test topography analysis functions"""
    if current_session is None:
        print("❌ 請先載入實驗會話 / Please load experiment session first")
        return
    
    topo_files = current_session.get_topo_files()
    if not topo_files:
        print("❌ 沒有找到拓撲檔案 / No topography files found")
        return
    
    file_key = topo_files[0]
    print(f"🔧 測試檔案: {file_key}")
    
    try:
        topo = current_session[file_key]
        data = topo.data
        
        print(f"✅ 檔案載入成功")
        print(f"   - 數據類型: {type(data).__name__}")
        print(f"   - 圖像尺寸: {data.shape}")
        print(f"   - X 範圍: {data.x_range} nm")
        print(f"   - Y 範圍: {data.y_range} nm")
        
        # 測試分析器 / Test analyzer
        analyzer = topo.analyzer
        print(f"✅ 分析器創建成功: {type(analyzer).__name__}")
        
        # 測試便利屬性 / Test convenience properties
        print(f"✅ 便利屬性測試:")
        print(f"   - topo.image.shape: {topo.image.shape}")
        print(f"   - topo.x_range: {topo.x_range} nm")
        print(f"   - topo.y_range: {topo.y_range} nm")
        print(f"   - topo.shape: {topo.shape}")
        
    except Exception as e:
        print(f"❌ 測試失敗: {str(e)}")
        import traceback
        traceback.print_exc()

def test_cits_analysis():
    """測試 CITS 分析功能 / Test CITS analysis functions"""
    if current_session is None:
        print("❌ 請先載入實驗會話 / Please load experiment session first")
        return
    
    cits_files = current_session.get_cits_files()
    if not cits_files:
        print("❌ 沒有找到 CITS 檔案 / No CITS files found")
        return
    
    file_key = cits_files[0]
    print(f"🔬 測試檔案: {file_key}")
    
    try:
        cits = current_session[file_key]
        data = cits.data
        
        print(f"✅ 檔案載入成功")
        print(f"   - 數據類型: {type(data).__name__}")
        print(f"   - 3D 數據尺寸: {data.shape}")
        print(f"   - 偏壓點數: {data.n_bias_points}")
        print(f"   - 偏壓範圍: {data.bias_range}")
        
        # 測試分析器 / Test analyzer
        analyzer = cits.analyzer
        print(f"✅ 分析器創建成功: {type(analyzer).__name__}")
        
        # 測試便利屬性和方法 / Test convenience properties and methods
        print(f"✅ 便利屬性測試:")
        print(f"   - cits.bias_values.shape: {cits.bias_values.shape}")
        print(f"   - cits.data_3d.shape: {cits.data_3d.shape}")
        
        # 測試偏壓切片 / Test bias slice
        bias_slice = cits.get_bias_slice(0)
        print(f"   - 偏壓切片 [0]: {bias_slice.shape}")
        
    except Exception as e:
        print(f"❌ 測試失敗: {str(e)}")
        import traceback
        traceback.print_exc()

# 分析功能測試按鈕 / Analysis function test buttons
print("🔧 分析功能測試 / Analysis Functions Test")
print("=" * 40)

test_topo_button = widgets.Button(
    description='🗺️ 測試拓撲分析 / Test Topo Analysis',
    button_style='info',
    layout=widgets.Layout(width='250px')
)

test_cits_button = widgets.Button(
    description='🔬 測試 CITS 分析 / Test CITS Analysis',
    button_style='info',
    layout=widgets.Layout(width='250px')
)

test_output = widgets.Output()

def on_test_topo_clicked(b):
    with test_output:
        clear_output()
        test_topography_analysis()

def on_test_cits_clicked(b):
    with test_output:
        clear_output()
        test_cits_analysis()

test_topo_button.on_click(on_test_topo_clicked)
test_cits_button.on_click(on_test_cits_clicked)

display(widgets.HBox([test_topo_button, test_cits_button]))
display(test_output)

🔧 分析功能測試 / Analysis Functions Test


Output()

## 📊 8. 記憶體和快取管理 / Memory and Cache Management

In [ ]:
def show_memory_info():
    """顯示記憶體使用資訊 / Show memory usage information"""
    if current_session is None:
        print("❌ 請先載入實驗會話 / Please load experiment session first")
        return
    
    memory_info = current_session.get_memory_info()
    
    print("📊 記憶體使用資訊 / Memory Usage Information")
    print("=" * 50)
    
    print(f"📁 總檔案數: {memory_info['total_files']}")
    print(f"📁 已載入檔案數: {memory_info['total_loaded']}")
    print(f"📦 代理快取大小: {memory_info['proxy_cache_size']}")
    
    print("\n📂 各類型快取資訊:")
    for cache_type, cache_info in memory_info.items():
        if isinstance(cache_info, dict) and 'cache_size' in cache_info:
            print(f"   {cache_type}:")
            print(f"     - 快取大小: {cache_info['cache_size']}/{cache_info['max_cache_size']}")
            print(f"     - 載入次數: {cache_info['load_count']}")
            print(f"     - 快取命中率: {cache_info['hit_rate']:.2%}")
            if cache_info['cached_files']:
                print(f"     - 已快取檔案: {', '.join(cache_info['cached_files'][:3])}")
                if len(cache_info['cached_files']) > 3:
                    print(f"       ... 等 {len(cache_info['cached_files'])} 個檔案")

def clear_all_caches():
    """清理所有快取 / Clear all caches"""
    if current_session is None:
        print("❌ 請先載入實驗會話 / Please load experiment session first")
        return
    
    try:
        current_session.clear_all_caches()
        print("✅ 所有快取已清理 / All caches cleared")
        
        # 顯示清理後的狀態 / Show state after clearing
        show_memory_info()
        
    except Exception as e:
        print(f"❌ 清理快取失敗 / Failed to clear caches: {str(e)}")

# 記憶體管理按鈕 / Memory management buttons
print("📊 記憶體和快取管理 / Memory and Cache Management")
print("=" * 50)

show_memory_button = widgets.Button(
    description='📊 顯示記憶體資訊 / Show Memory Info',
    button_style='info',
    layout=widgets.Layout(width='250px')
)

clear_cache_button = widgets.Button(
    description='🧹 清理快取 / Clear Cache',
    button_style='warning',
    layout=widgets.Layout(width='200px')
)

memory_output = widgets.Output()

def on_show_memory_clicked(b):
    with memory_output:
        clear_output()
        show_memory_info()

def on_clear_cache_clicked(b):
    with memory_output:
        clear_output()
        clear_all_caches()

show_memory_button.on_click(on_show_memory_clicked)
clear_cache_button.on_click(on_clear_cache_clicked)

display(widgets.HBox([show_memory_button, clear_cache_button]))
display(memory_output)

📊 記憶體和快取管理 / Memory and Cache Management


Output()

## 🎯 9. 綜合測試和演示 / Comprehensive Test and Demo

In [ ]:
def comprehensive_demo():
    """綜合演示新架構功能 / Comprehensive demo of new architecture"""
    if current_session is None:
        print("❌ 請先載入實驗會話 / Please load experiment session first")
        return
    
    print("🎯 新架構綜合演示 / Comprehensive New Architecture Demo")
    print("=" * 60)
    
    try:
        # 1. 顯示會話摘要 / Show session summary
        print("\n1️⃣ 會話摘要 / Session Summary:")
        summary = current_session.get_session_summary()
        print(f"   實驗名稱: {summary['experiment_name']}")
        print(f"   總檔案數: {summary['files_summary']['total_available']}")
        
        # 2. 演示檔案存取 / Demo file access
        print("\n2️⃣ 檔案存取演示 / File Access Demo:")
        available = current_session.available_files
        
        # 拓撲檔案 / Topography file
        if available['topo']:
            topo_key = available['topo'][0]
            topo = current_session[topo_key]
            print(f"   拓撲檔案: {topo_key}")
            print(f"   - IDE 友好存取: topo.data.x_range = {topo.data.x_range} nm")
            print(f"   - 圖像尺寸: {topo.image.shape}")
            
        # CITS 檔案 / CITS file
        if available['cits']:
            cits_key = available['cits'][0]
            cits = current_session[cits_key]
            print(f"   CITS 檔案: {cits_key}")
            print(f"   - IDE 友好存取: cits.data.n_bias_points = {cits.data.n_bias_points}")
            print(f"   - 3D 數據形狀: {cits.data_3d.shape}")
        
        # 3. 演示搜尋功能 / Demo search functionality
        print("\n3️⃣ 搜尋功能演示 / Search Functionality Demo:")
        topo_files = current_session.find_files_by_signal_type("Topo")
        fwd_files = current_session.find_files_by_direction("Fwd")
        print(f"   Topo 訊號檔案: {len(topo_files)} 個")
        print(f"   正向掃描檔案: {len(fwd_files)} 個")
        
        # 4. 演示批次操作 / Demo batch operations
        print("\n4️⃣ 批次操作演示 / Batch Operations Demo:")
        topo_files = current_session.get_topo_files()
        if len(topo_files) >= 2:
            batch_keys = topo_files[:2]
            results = current_session.load_multiple_files(batch_keys)
            success_count = sum(1 for r in results.values() if r.metadata.get('success', False))
            print(f"   批次載入 {len(batch_keys)} 個檔案，成功 {success_count} 個")
        
        # 5. 演示記憶體管理 / Demo memory management
        print("\n5️⃣ 記憶體管理演示 / Memory Management Demo:")
        memory_info = current_session.get_memory_info()
        print(f"   已載入檔案: {memory_info['total_loaded']}/{memory_info['total_files']}")
        
        # 快取命中率統計 / Cache hit rate statistics
        total_hits = 0
        total_misses = 0
        for cache_type, cache_info in memory_info.items():
            if isinstance(cache_info, dict) and 'cache_hits' in cache_info:
                total_hits += cache_info['cache_hits']
                total_misses += cache_info['cache_misses']
        
        if total_hits + total_misses > 0:
            overall_hit_rate = total_hits / (total_hits + total_misses)
            print(f"   總快取命中率: {overall_hit_rate:.2%}")
        
        print("\n✅ 綜合演示完成! / Comprehensive demo completed!")
        print("\n🌟 新架構優勢 / New Architecture Advantages:")
        print("   ✓ IDE 友好的型別提示")
        print("   ✓ 直覺的屬性存取")
        print("   ✓ 智能快取管理")
        print("   ✓ 統一的錯誤處理")
        print("   ✓ 模組化設計")
        
    except Exception as e:
        print(f"❌ 演示過程中發生錯誤: {str(e)}")
        import traceback
        traceback.print_exc()

# 綜合演示按鈕 / Comprehensive demo button
print("🎯 綜合測試和演示 / Comprehensive Test and Demo")
print("=" * 50)

demo_button = widgets.Button(
    description='🎯 執行綜合演示 / Run Comprehensive Demo',
    button_style='success',
    layout=widgets.Layout(width='300px')
)

demo_output = widgets.Output()

def on_demo_clicked(b):
    with demo_output:
        clear_output()
        comprehensive_demo()

demo_button.on_click(on_demo_clicked)

display(demo_button)
display(demo_output)

🎯 綜合測試和演示 / Comprehensive Test and Demo


Button(button_style='success', description='🎯 執行綜合演示 / Run Comprehensive Demo', layout=Layout(width='300px'), …

Output()

## 📝 10. 總結和下一步 / Summary and Next Steps

### ✅ 測試完成項目 / Completed Test Items

1. **基本功能測試 / Basic Functionality Tests**
   - ExperimentSession 初始化
   - 檔案載入和解析
   - IDE 友好的屬性存取

2. **視覺化測試 / Visualization Tests**
   - 拓撲圖繪製（原始和平坦化）
   - CITS 偏壓切片視覺化
   - I-V 曲線繪製

3. **進階功能測試 / Advanced Feature Tests**
   - 檔案搜尋和篩選
   - 批次操作
   - 記憶體和快取管理

### 🎯 新架構優勢驗證 / New Architecture Advantages Verified

- ✅ **IDE 友好**: 完整的型別提示和自動完成
- ✅ **直覺存取**: `session['file'].data.attribute` 語法
- ✅ **智能快取**: 自動的 LRU 快取管理
- ✅ **統一格式**: 標準化的 ParseResult 和資料模型
- ✅ **錯誤處理**: 完整的例外處理和錯誤報告

### 📋 下一步工作 / Next Steps

1. **API 整合** - 更新 `api_mvp.py` 使用新架構
2. **前端整合** - 確保前端能無縫使用新後端
3. **效能優化** - 針對大型數據檔案的載入優化
4. **單元測試** - 建立完整的測試套件
5. **文檔更新** - 更新使用指南和 API 文檔

### 🚀 使用建議 / Usage Recommendations

1. 使用 Widget 介面進行互動式分析
2. 利用新架構的型別提示提高開發效率
3. 善用搜尋和批次功能處理大量檔案
4. 定期檢查記憶體使用狀況
5. 充分利用 Plotly 的互動式視覺化功能